In [79]:
import os
import re
from PIL import Image
import h5py
import numpy as np
# import sys
# !conda install --yes --prefix {sys.prefix} ipywidgets # install in the current conda environment
# !jupyter nbextension enable --py widgetsnbextension 
# Then restart jupyter
from tqdm.notebook import tqdm
from numba import jit, njit, cuda

In [38]:
path_tiles_qp = "/media/visiopharm5/WDRed(backup)/qupath/tiles_"
path_patch_seg = "/media/visiopharm5/WDGold/deeplearning/MIL/CLAM/results/patches"
path_patch_anno = "/media/visiopharm5/WDGold/deeplearning/MIL/CLAM/results/patches_tumor"

In [39]:
slide_id = []
tile_id = []
mask_id =  []
for root, dirs, files in os.walk(path_tiles_qp):
    for name in sorted(dirs):
        slide_id.append(name)
    tmp_tile = []
    tmp_mask = []
    if len(files) != 0:
        for file in files:
            if file.endswith(".tif"):
                tmp_tile.append(file)
            elif file.endswith(".png"):
                tmp_mask.append(file)
        tile_id.append(tmp_tile)
        mask_id.append(tmp_mask)  

In [40]:
print(slide_id[14])

TCGA-5R-AA1C-01Z-00-DX1.DC038B55-4002-406D-B9DD-2A4BFDB03A61


In [16]:
print(tile_id[0:3])

[['TCGA-2V-A95S-01Z-00-DX1.9DFA6FC7-87A6-4C14-9A39-E3F12B01C4D4 [x=10240,y=10240,w=512,h=512].tif', 'TCGA-2V-A95S-01Z-00-DX1.9DFA6FC7-87A6-4C14-9A39-E3F12B01C4D4 [x=10240,y=10752,w=512,h=512].tif', 'TCGA-2V-A95S-01Z-00-DX1.9DFA6FC7-87A6-4C14-9A39-E3F12B01C4D4 [x=10240,y=11264,w=512,h=512].tif', 'TCGA-2V-A95S-01Z-00-DX1.9DFA6FC7-87A6-4C14-9A39-E3F12B01C4D4 [x=22528,y=4608,w=512,h=512].tif', 'TCGA-2V-A95S-01Z-00-DX1.9DFA6FC7-87A6-4C14-9A39-E3F12B01C4D4 [x=22528,y=5120,w=512,h=512].tif', 'TCGA-2V-A95S-01Z-00-DX1.9DFA6FC7-87A6-4C14-9A39-E3F12B01C4D4 [x=22528,y=5632,w=512,h=512].tif', 'TCGA-2V-A95S-01Z-00-DX1.9DFA6FC7-87A6-4C14-9A39-E3F12B01C4D4 [x=22528,y=6144,w=512,h=512].tif', 'TCGA-2V-A95S-01Z-00-DX1.9DFA6FC7-87A6-4C14-9A39-E3F12B01C4D4 [x=33280,y=4608,w=512,h=512].tif', 'TCGA-2V-A95S-01Z-00-DX1.9DFA6FC7-87A6-4C14-9A39-E3F12B01C4D4 [x=33280,y=5120,w=512,h=512].tif', 'TCGA-2V-A95S-01Z-00-DX1.9DFA6FC7-87A6-4C14-9A39-E3F12B01C4D4 [x=33280,y=5632,w=512,h=512].tif', 'TCGA-2V-A95S-01Z-00-DX1.

In [17]:
print(mask_id[0:3])

[['TCGA-2V-A95S-01Z-00-DX1.9DFA6FC7-87A6-4C14-9A39-E3F12B01C4D4 [x=10240,y=10240,w=512,h=512]-labelled.png', 'TCGA-2V-A95S-01Z-00-DX1.9DFA6FC7-87A6-4C14-9A39-E3F12B01C4D4 [x=10240,y=10752,w=512,h=512]-labelled.png', 'TCGA-2V-A95S-01Z-00-DX1.9DFA6FC7-87A6-4C14-9A39-E3F12B01C4D4 [x=10240,y=11264,w=512,h=512]-labelled.png', 'TCGA-2V-A95S-01Z-00-DX1.9DFA6FC7-87A6-4C14-9A39-E3F12B01C4D4 [x=10240,y=11776,w=512,h=512]-labelled.png', 'TCGA-2V-A95S-01Z-00-DX1.9DFA6FC7-87A6-4C14-9A39-E3F12B01C4D4 [x=22528,y=4608,w=512,h=512]-labelled.png', 'TCGA-2V-A95S-01Z-00-DX1.9DFA6FC7-87A6-4C14-9A39-E3F12B01C4D4 [x=22528,y=5120,w=512,h=512]-labelled.png', 'TCGA-2V-A95S-01Z-00-DX1.9DFA6FC7-87A6-4C14-9A39-E3F12B01C4D4 [x=22528,y=5632,w=512,h=512]-labelled.png', 'TCGA-2V-A95S-01Z-00-DX1.9DFA6FC7-87A6-4C14-9A39-E3F12B01C4D4 [x=22528,y=6144,w=512,h=512]-labelled.png', 'TCGA-2V-A95S-01Z-00-DX1.9DFA6FC7-87A6-4C14-9A39-E3F12B01C4D4 [x=33280,y=4608,w=512,h=512]-labelled.png', 'TCGA-2V-A95S-01Z-00-DX1.9DFA6FC7-87A6-4

In [82]:
def main(s:int=0):
    for i in tqdm(range(s, len(tile_id))): # for each slide / bag
        if os.path.isfile(os.path.join(path_patch_anno, slide_id[i]+'.h5')):
            print("There is this file:")
            print(str(i)+": "+slide_id[i])
        else:
            with h5py.File(os.path.join(path_patch_anno, slide_id[i]+'.h5'), "w") as f: # create a h5 file for each bag
                init = True

                for j in tqdm(range(len(tile_id[i]))): # for each patch
                    mask = np.asarray(Image.open(os.path.join(path_tiles_qp, slide_id[i], tile_id[i][j]
                                                              .replace(".tif","-labelled.png"))))
                    if sum(sum(mask==1)) >= 32768: # only annotated higher than 50% will be considered
                        # coords
                        x = int(re.split("=|,",tile_id[i][j])[1])//2
                        y = int(re.split("=|,",tile_id[i][j])[3])//2
                        if init:
                            coords = [x, y]
                        else:
                            coords = np.vstack((coords, [x, y]))

                        # imgs
                        if init:
                            imgs = np.asarray(Image.open(os.path.join(path_tiles_qp, slide_id[i], tile_id[i][j])))
                            imgs = imgs[np.newaxis, :, :, :]
                            init = False
                        else:
                            imgs = np.vstack((imgs, np.asarray(Image.open(os.path.join(path_tiles_qp, slide_id[i], 
                                                                                       tile_id[i][j])))[np.newaxis, :, :, :]))
                coords = coords.astype(np.int32) # convert from string to int32
                f.create_dataset("coords", data=coords)
                imgs = f.create_dataset("imgs", data=imgs)
                with h5py.File(os.path.join(path_patch_seg, slide_id[i]+".h5"), "r") as f_ref:
                    for k in range(len(f_ref["imgs"].attrs.values())): # coords have no attributes
                            imgs.attrs[list(f_ref["imgs"].attrs.keys())[k]] = list(f_ref["imgs"].attrs.values())[k]

In [ ]:
print(main(14))